### Spark Moive Recommendation 
In this notebook, we will use an Alternating Least Squares (ALS) algorithm with Spark APIs to predict the ratings for the movies in [MovieLens small dataset](https://grouplens.org/datasets/movielens/latest/)

In [0]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import math
%matplotlib inline

In [0]:
import os
os.environ["PYSPARK_PYTHON"] = "python3"

## Part1: Data ETL and Data Exploration

In [0]:
# Please donwload your data from the website then upload to databricks at first https://grouplens.org/datasets/movielens/latest/
# 参考hw1，自己完善 :) 



In [0]:
movies_df = spark.read.load("/FileStore/tables/movies.csv", format='csv', header = True)
ratings_df = spark.read.load("/FileStore/tables/ratings.csv", format='csv', header = True)
links_df = spark.read.load("/FileStore/tables/links.csv", format='csv', header = True)
tags_df = spark.read.load("/FileStore/tables/tags.csv", format='csv', header = True)

In [0]:
movies_df.show(5)

+-------+--------------------+--------------------+
|movieId|               title|              genres|
+-------+--------------------+--------------------+
|      1|    Toy Story (1995)|Adventure|Animati...|
|      2|      Jumanji (1995)|Adventure|Childre...|
|      3|Grumpier Old Men ...|      Comedy|Romance|
|      4|Waiting to Exhale...|Comedy|Drama|Romance|
|      5|Father of the Bri...|              Comedy|
+-------+--------------------+--------------------+
only showing top 5 rows



In [0]:
ratings_df.show(10)

+------+-------+------+---------+
|userId|movieId|rating|timestamp|
+------+-------+------+---------+
|     1|      1|   4.0|964982703|
|     1|      3|   4.0|964981247|
|     1|      6|   4.0|964982224|
|     1|     47|   5.0|964983815|
|     1|     50|   5.0|964982931|
|     1|     70|   3.0|964982400|
|     1|    101|   5.0|964980868|
|     1|    110|   4.0|964982176|
|     1|    151|   5.0|964984041|
|     1|    157|   5.0|964984100|
+------+-------+------+---------+
only showing top 10 rows



In [0]:
links_df.show(5)

+-------+-------+------+
|movieId| imdbId|tmdbId|
+-------+-------+------+
|      1|0114709|   862|
|      2|0113497|  8844|
|      3|0113228| 15602|
|      4|0114885| 31357|
|      5|0113041| 11862|
+-------+-------+------+
only showing top 5 rows



In [0]:
tags_df.show(5)

+------+-------+---------------+----------+
|userId|movieId|            tag| timestamp|
+------+-------+---------------+----------+
|     2|  60756|          funny|1445714994|
|     2|  60756|Highly quotable|1445714996|
|     2|  60756|   will ferrell|1445714992|
|     2|  89774|   Boxing story|1445715207|
|     2|  89774|            MMA|1445715200|
+------+-------+---------------+----------+
only showing top 5 rows



In [0]:
tmp1 = ratings_df.groupBy("userID").count().toPandas()['count'].min()
tmp2 = ratings_df.groupBy("movieId").count().toPandas()['count'].min()
print('For the users that rated movies and the movies that were rated:')
print('Minimum number of ratings per user is {}'.format(tmp1))
print('Minimum number of ratings per movie is {}'.format(tmp2))

For the users that rated movies and the movies that were rated:
Minimum number of ratings per user is 20
Minimum number of ratings per movie is 1


In [0]:
tmp1 = sum(ratings_df.groupBy("movieId").count().toPandas()['count'] == 1)
tmp2 = ratings_df.select('movieId').distinct().count()
print('{} out of {} movies are rated by only one user'.format(tmp1, tmp2))

3446 out of 9724 movies are rated by only one user


## Part 1: Spark SQL and OLAP 

In [0]:
movies_df.registerTempTable("movies")
ratings_df.registerTempTable("ratings")
links_df.registerTempTable("links")
tags_df.registerTempTable("tags")

/databricks/spark/python/pyspark/sql/dataframe.py:331: FutureWarning: Deprecated in 2.0, use createOrReplaceTempView instead.
  warnings.warn("Deprecated in 2.0, use createOrReplaceTempView instead.", FutureWarning)


### Q1: The number of Users

In [0]:
q1_result=spark.sql("Select Count(Distinct userId) as Number_of_Users from ratings")
q1_result.show()

+---------------+
|Number_of_Users|
+---------------+
|            610|
+---------------+



### Q2: The number of Movies

In [0]:
q3_result_1=spark.sql("Select Count(movieId) as Number_of_Rated_Moives From movies Where movieID in (Select movieId From ratings)")
q3_result_1.show()

+----------------------+
|Number_of_Rated_Moives|
+----------------------+
|                  9724|
+----------------------+



### Q3:  How many movies are rated by users? List movies not rated before

In [0]:
q3_result_2=spark.sql("Select movieId, title From movies Where movieID not in (Select movieId From ratings)")
q3_result_2.show()

+-------+--------------------+
|movieId|               title|
+-------+--------------------+
|   1076|Innocents, The (1...|
|   2939|      Niagara (1953)|
|   3338|For All Mankind (...|
|   3456|Color of Paradise...|
|   4194|I Know Where I'm ...|
|   5721|  Chosen, The (1981)|
|   6668|Road Home, The (W...|
|   6849|      Scrooge (1970)|
|   7020|        Proof (1991)|
|   7792|Parallax View, Th...|
|   8765|This Gun for Hire...|
|  25855|Roaring Twenties,...|
|  26085|Mutiny on the Bou...|
|  30892|In the Realms of ...|
|  32160|Twentieth Century...|
|  32371|Call Northside 77...|
|  34482|Browning Version,...|
|  85565|  Chalet Girl (2011)|
+-------+--------------------+



### Q4: List Movie Genres

In [0]:
q4_result=spark.sql("Select Distinct explode(split(genres,'[|]')) as genres From movies Order by 1")
q4_result.show()

+------------------+
|            genres|
+------------------+
|(no genres listed)|
|            Action|
|         Adventure|
|         Animation|
|          Children|
|            Comedy|
|             Crime|
|       Documentary|
|             Drama|
|           Fantasy|
|         Film-Noir|
|            Horror|
|              IMAX|
|           Musical|
|           Mystery|
|           Romance|
|            Sci-Fi|
|          Thriller|
|               War|
|           Western|
+------------------+



In [0]:
%sql

### Q5: Movie for Each Category

In [0]:
q5_result_1=spark.sql("Select genres,Count(movieId) as Number_of_Moives From(Select explode(split(genres,'[|]')) as genres, movieId From movies) Group By 1 Order by 2 DESC")
q5_result_1.show()

+------------------+----------------+
|            genres|Number_of_Moives|
+------------------+----------------+
|             Drama|            4361|
|            Comedy|            3756|
|          Thriller|            1894|
|            Action|            1828|
|           Romance|            1596|
|         Adventure|            1263|
|             Crime|            1199|
|            Sci-Fi|             980|
|            Horror|             978|
|           Fantasy|             779|
|          Children|             664|
|         Animation|             611|
|           Mystery|             573|
|       Documentary|             440|
|               War|             382|
|           Musical|             334|
|           Western|             167|
|              IMAX|             158|
|         Film-Noir|              87|
|(no genres listed)|              34|
+------------------+----------------+



In [0]:
%sql 

## Part2: Spark ALS based approach for training model
We will use an Spark ML to predict the ratings, so let's reload "ratings.csv" using ``sc.textFile`` and then convert it to the form of (user, item, rating) tuples.

In [0]:
ratings_df.show()

+------+-------+------+---------+
|userId|movieId|rating|timestamp|
+------+-------+------+---------+
|     1|      1|   4.0|964982703|
|     1|      3|   4.0|964981247|
|     1|      6|   4.0|964982224|
|     1|     47|   5.0|964983815|
|     1|     50|   5.0|964982931|
|     1|     70|   3.0|964982400|
|     1|    101|   5.0|964980868|
|     1|    110|   4.0|964982176|
|     1|    151|   5.0|964984041|
|     1|    157|   5.0|964984100|
|     1|    163|   5.0|964983650|
|     1|    216|   5.0|964981208|
|     1|    223|   3.0|964980985|
|     1|    231|   5.0|964981179|
|     1|    235|   4.0|964980908|
|     1|    260|   5.0|964981680|
|     1|    296|   3.0|964982967|
|     1|    316|   3.0|964982310|
|     1|    333|   5.0|964981179|
|     1|    349|   4.0|964982563|
+------+-------+------+---------+
only showing top 20 rows



In [0]:
movie_ratings=ratings_df.drop('timestamp')

In [0]:
# Data type convert
from pyspark.sql.types import IntegerType, FloatType
movie_ratings = movie_ratings.withColumn("userId", movie_ratings["userId"].cast(IntegerType()))
movie_ratings = movie_ratings.withColumn("movieId", movie_ratings["movieId"].cast(IntegerType()))
movie_ratings = movie_ratings.withColumn("rating", movie_ratings["rating"].cast(FloatType()))

In [0]:
movie_ratings.show()

+------+-------+------+
|userId|movieId|rating|
+------+-------+------+
|     1|      1|   4.0|
|     1|      3|   4.0|
|     1|      6|   4.0|
|     1|     47|   5.0|
|     1|     50|   5.0|
|     1|     70|   3.0|
|     1|    101|   5.0|
|     1|    110|   4.0|
|     1|    151|   5.0|
|     1|    157|   5.0|
|     1|    163|   5.0|
|     1|    216|   5.0|
|     1|    223|   3.0|
|     1|    231|   5.0|
|     1|    235|   4.0|
|     1|    260|   5.0|
|     1|    296|   3.0|
|     1|    316|   3.0|
|     1|    333|   5.0|
|     1|    349|   4.0|
+------+-------+------+
only showing top 20 rows



### ALS Model Selection and Evaluation

With the ALS model, we can use a grid search to find the optimal hyperparameters.

In [0]:
# import package
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.recommendation import ALS
from pyspark.ml.tuning import CrossValidator,ParamGridBuilder

In [0]:
#Create test and train set
(training, test) = movie_ratings.randomSplit([0.8, 0.2])

In [0]:
#Create ALS model
als = ALS(maxIter=5, rank=10, regParam=0.01, userCol="userId", itemCol="movieId", ratingCol="rating",
          coldStartStrategy="drop")

In [0]:
#Tune model using ParamGridBuilder
paramGrid = (ParamGridBuilder()
             .addGrid(als.regParam, [0.1, 0.3])  # Try fewer values, e.g., 0.1 and 0.3
             .addGrid(als.rank, [10])            # Test only rank=10 to start
             .addGrid(als.maxIter, [5])          # Fix maxIter to 5
             .build())


In [0]:
# Define evaluator as RMSE
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating",
                                predictionCol="prediction")

In [0]:
# Build Cross validation 
cv = CrossValidator(estimator=als, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=3)


In [0]:
# Fit the ALS model
cvModel = cv.fit(training)

In [0]:
#Extract best model from the tuning exercise using ParamGridBuilder
bestModel=cvModel.bestModel

### Model testing
And finally, make a prediction and check the testing error.

In [0]:
#Generate predictions and evaluate using RMSE
predictions=bestModel.transform(test)
rmse = evaluator.evaluate(predictions)

In [0]:
#Print evaluation metrics and model parameters
print ("RMSE = "+str(rmse))
print ("**Best Model**")
print (" Rank:"), 
print (" MaxIter:"), 
print (" RegParam:"), 

RMSE = 0.9146168868010629
**Best Model**
 Rank:
 MaxIter:
 RegParam:
Out[39]: (None,)

In [0]:
predictions.show()

+------+-------+------+----------+
|userId|movieId|rating|prediction|
+------+-------+------+----------+
|     1|      6|   4.0|  4.414794|
|     1|     50|   5.0|   4.81697|
|     1|     70|   3.0|  4.018732|
|     1|    223|   3.0| 4.4153004|
|     1|    333|   5.0| 4.1544886|
|     1|    367|   4.0| 3.5648677|
|     1|    441|   4.0| 4.4232807|
|     1|    552|   4.0| 3.5246463|
|     1|    590|   4.0| 4.2634654|
|     1|    661|   5.0| 3.7678907|
|     1|    943|   4.0| 4.4622855|
|     1|   1009|   3.0| 3.3845632|
|     1|   1023|   5.0| 3.8209221|
|     1|   1031|   5.0| 3.9315696|
|     1|   1032|   5.0| 3.7770712|
|     1|   1090|   4.0|  4.574177|
|     1|   1127|   4.0|  3.861291|
|     1|   1197|   5.0|  4.684467|
|     1|   1198|   5.0|  4.681014|
|     1|   1213|   5.0| 4.6583586|
+------+-------+------+----------+
only showing top 20 rows



### Model apply and see the performance

In [0]:
alldata=bestModel.transform(movie_ratings)
rmse = evaluator.evaluate(alldata)
print ("RMSE = "+str(rmse))

RMSE = 0.8303056903433411


In [0]:
alldata.registerTempTable("alldata")

In [0]:
%sql select * from alldata

userId movieId rating prediction 1 1 4.0 4.2983937 1 3 4.0 3.5502489 1 6 4.0 4.414794 1 47 5.0 4.4428205 1 50 5.0 4.81697 1 70 3.0 4.018732 1 101 5.0 4.3310103 1 110 4.0 4.4655643 1 151 5.0 3.9751935 1 157 5.0 3.4518933 1 163 5.0 4.29975 1 216 5.0 3.8564801 1 223 3.0 4.4153004 1 231 5.0 3.482601 1 235 4.0 4.115503 1 260 5.0 4.728784 1 296 3.0 4.6522193 1 316 3.0 3.7228653 1 333 5.0 4.1544886 1 349 4.0 3.9375205 1 356 4.0 4.6676245 1 362 5.0 3.88359 1 367 4.0 3.5648677 1 423 3.0 3.13679 1 441 4.0 4.4232807 1 457 5.0 4.461871 1 480 4.0 4.196642 1 500 3.0 3.8174634 1 527 5.0 4.7035723 1 543 4.0 3.8313582 1 552 4.0 3.5246463 1 553 5.0 4.3179274 1 590 4.0 4.2634654 1 592 4.0 3.7840908 1 593 4.0 4.6606627 1 596 5.0 4.0248294 1 608 5.0 4.5895987 1 648 3.0 3.8592284 1 661 5.0 3.7678907 1 673 3.0 3.2082381 1 733 4.0 3.9893847 1 736 3.0 3.5411813 1 780 3.0 3.774298 1 804 4.0 3.639513 1 919 5.0 4.4044876 1 923 5.0 4.4456143 1 940 5.0 4.5667586 1 943 4.0 4.4622855 1 954 5.0 4.6446753 1 1009 3.0 3.3845632 1 1023 5.0 3.8209221 1 1024 5.0 4.061979 1 1025 5.0 4.1289725 1 1029 5.0 3.8364646 1 1030 3.0 2.962204 1 1031 5.0 3.9315696 1 1032 5.0 3.7770712 1 1042 4.0 3.7019968 1 1049 5.0 3.8584998 1 1060 4.0 4.2278786 1 1073 5.0 4.234695 1 1080 5.0 4.3648205 1 1089 5.0 4.6459684 1 1090 4.0 4.574177 1 1092 5.0 3.625608 1 1097 5.0 4.228727 1 1127 4.0 3.861291 1 1136 5.0 4.758982 1 1196 5.0 4.706216 1 1197 5.0 4.684467 1 1198 5.0 4.681014 1 1206 5.0 4.509072 1 1208 4.0 4.6952934 1 1210 5.0 4.534934 1 1213 5.0 4.6583586 1 1214 4.0 4.455938 1 1219 2.0 4.588829 1 1220 5.0 4.247949 1 1222 5.0 4.585179 1 1224 5.0 4.2521367 1 1226 5.0 3.5701308 1 1240 5.0 4.373079 1 1256 5.0 4.2824817 1 1258 3.0 4.5233326 1 1265 4.0 4.433615 1 1270 5.0 4.479471 1 1275 5.0 4.224482 1 1278 5.0 4.5553894 1 1282 5.0 4.1031876 1 1291 5.0 4.536492 1 1298 5.0 4.1230235 1 1348 4.0 3.999546 1 1377 3.0 3.4208522 1 1396 3.0 3.9544683 1 1408 3.0 4.1418853 1 1445 3.0 2.7380319 1 1473 4.0 3.7666776 1 1500 4.0 4.119432 1 1517 5.0 3.9971557 1 1552 4.0 3.488657 1 1573 5.0 3.7726607 1 1580 3.0 4.015643 1 1587 5.0 3.841214 1 1617 5.0 4.502282 1 1620 4.0 3.769328 1 1625 5.0 4.102431 1 1644 3.0 2.462885 1 1676 3.0 3.5358326 1 1732 5.0 4.430957 1 1777 4.0 3.8787513 1 1793 4.0 3.8956347 1 1804 5.0 3.9890938 1 1805 4.0 3.3880196 1 1920 4.0 3.4012914 1 1927 5.0 4.367138 1 1954 5.0 4.343986 1 1967 4.0 4.4450645 1 2000 4.0 4.1275845 1 2005 5.0 4.113149 1 2012 4.0 3.7643514 1 2018 5.0 3.9586468 1 2028 4.0 4.5333743 1 2033 5.0 4.33115 1 2046 4.0 3.431322 1 2048 5.0 3.576335 1 2054 4.0 3.0863621 1 2058 5.0 3.821169 1 2078 5.0 4.336316 1 2090 5.0 3.9248023 1 2093 3.0 3.926834 1 2094 5.0 3.6248903 1 2096 4.0 3.8133433 1 2099 4.0 3.9780436 1 2105 4.0 3.7778864 1 2115 5.0 4.1336126 1 2116 5.0 3.5122097 1 2137 5.0 3.876001 1 2139 5.0 4.0431614 1 2141 5.0 3.7022367 1 2143 4.0 3.5534234 1 2161 5.0 4.039898 1 2174 4.0 4.1084614 1 2193 4.0 3.839997 1 2253 2.0 2.754838 1 2268 4.0 4.2553854 1 2273 4.0 3.6829474 1 2291 5.0 4.2335215 1 2329 5.0 4.631743 1 2338 2.0 2.1443937 1 2353 5.0 3.8634682 1 2366 4.0 4.156075 1 2387 5.0 3.929341 1 2389 2.0 2.2834864 1 2395 5.0 4.2543106 1 2406 4.0 3.9088652 1 2414 3.0 3.7798522 1 2427 5.0 4.026966 1 2450 4.0 2.576334 1 2459 5.0 3.6631691 1 2470 5.0 3.4916139 1 2478 4.0 3.488493 1 2492 4.0 3.1518612 1 2502 5.0 4.6172066 1 2528 3.0 3.6484635 1 2529 5.0 4.394835 1 2542 5.0 4.5227685 1 2571 5.0 4.711994 1 2580 5.0 4.4016 1 2596 5.0 4.04576 1 2616 4.0 3.3383758 1 2617 2.0 3.6753252 1 2628 4.0 3.4942415 1 2640 4.0 4.109537 1 2641 5.0 3.3331912 1 2644 4.0 3.5574713 1 2648 4.0 4.1113706 1 2654 5.0 3.7229226 1 2657 3.0 3.7157426 1 2692 5.0 4.4603376 1 2700 5.0 4.436193 1 2716 5.0 4.2781415 1 2761 5.0 4.5104194 1 2797 4.0 4.1820364 1 2826 4.0 3.088358 1 2858 5.0 4.488807 1 2872 5.0 3.8234096 1 2899 5.0 3.7154589 1 2916 4.0 4.1889615 1 2944 5.0 4.294649 1 2947 5.0 4.3117857 1 2948 5.0 4.2857814 1 2949 5.0 4.126015 1 2959 5.0 4.7710977 1 2985 4.0 4.0376368 1 2987 5.0 4.083763 1 2991 5.0 4.

In [0]:
%sql select * from movies join alldata on movies.movieId=alldata.movieId

movieId title genres userId movieId rating prediction 1 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 1 1 4.0 4.2983937 3 Grumpier Old Men (1995) Comedy|Romance 1 3 4.0 3.5502489 6 Heat (1995) Action|Crime|Thriller 1 6 4.0 4.414794 47 Seven (a.k.a. Se7en) (1995) Mystery|Thriller 1 47 5.0 4.4428205 50 Usual Suspects, The (1995) Crime|Mystery|Thriller 1 50 5.0 4.81697 70 From Dusk Till Dawn (1996) Action|Comedy|Horror|Thriller 1 70 3.0 4.018732 101 Bottle Rocket (1996) Adventure|Comedy|Crime|Romance 1 101 5.0 4.3310103 110 Braveheart (1995) Action|Drama|War 1 110 4.0 4.4655643 151 Rob Roy (1995) Action|Drama|Romance|War 1 151 5.0 3.9751935 157 Canadian Bacon (1995) Comedy|War 1 157 5.0 3.4518933 163 Desperado (1995) Action|Romance|Western 1 163 5.0 4.29975 216 Billy Madison (1995) Comedy 1 216 5.0 3.8564801 223 Clerks (1994) Comedy 1 223 3.0 4.4153004 231 Dumb & Dumber (Dumb and Dumber) (1994) Adventure|Comedy 1 231 5.0 3.482601 235 Ed Wood (1994) Comedy|Drama 1 235 4.0 4.115503 260 Star Wars: Episode IV - A New Hope (1977) Action|Adventure|Sci-Fi 1 260 5.0 4.728784 296 Pulp Fiction (1994) Comedy|Crime|Drama|Thriller 1 296 3.0 4.6522193 316 Stargate (1994) Action|Adventure|Sci-Fi 1 316 3.0 3.7228653 333 Tommy Boy (1995) Comedy 1 333 5.0 4.1544886 349 Clear and Present Danger (1994) Action|Crime|Drama|Thriller 1 349 4.0 3.9375205 356 Forrest Gump (1994) Comedy|Drama|Romance|War 1 356 4.0 4.6676245 362 Jungle Book, The (1994) Adventure|Children|Romance 1 362 5.0 3.88359 367 Mask, The (1994) Action|Comedy|Crime|Fantasy 1 367 4.0 3.5648677 423 Blown Away (1994) Action|Thriller 1 423 3.0 3.13679 441 Dazed and Confused (1993) Comedy 1 441 4.0 4.4232807 457 Fugitive, The (1993) Thriller 1 457 5.0 4.461871 480 Jurassic Park (1993) Action|Adventure|Sci-Fi|Thriller 1 480 4.0 4.196642 500 Mrs. Doubtfire (1993) Comedy|Drama 1 500 3.0 3.8174634 527 Schindler's List (1993) Drama|War 1 527 5.0 4.7035723 543 So I Married an Axe Murderer (1993) Comedy|Romance|Thriller 1 543 4.0 3.8313582 552 Three Musketeers, The (1993) Action|Adventure|Comedy|Romance 1 552 4.0 3.5246463 553 Tombstone (1993) Action|Drama|Western 1 553 5.0 4.3179274 590 Dances with Wolves (1990) Adventure|Drama|Western 1 590 4.0 4.2634654 592 Batman (1989) Action|Crime|Thriller 1 592 4.0 3.7840908 593 Silence of the Lambs, The (1991) Crime|Horror|Thriller 1 593 4.0 4.6606627 596 Pinocchio (1940) Animation|Children|Fantasy|Musical 1 596 5.0 4.0248294 608 Fargo (1996) Comedy|Crime|Drama|Thriller 1 608 5.0 4.5895987 648 Mission: Impossible (1996) Action|Adventure|Mystery|Thriller 1 648 3.0 3.8592284 661 James and the Giant Peach (1996) Adventure|Animation|Children|Fantasy|Musical 1 661 5.0 3.7678907 673 Space Jam (1996) Adventure|Animation|Children|Comedy|Fantasy|Sci-Fi 1 673 3.0 3.2082381 733 Rock, The (1996) Action|Adventure|Thriller 1 733 4.0 3.9893847 736 Twister (1996) Action|Adventure|Romance|Thriller 1 736 3.0 3.5411813 780 Independence Day (a.k.a. ID4) (1996) Action|Adventure|Sci-Fi|Thriller 1 780 3.0 3.774298 804 She's the One (1996) Comedy|Romance 1 804 4.0 3.639513 919 Wizard of Oz, The (1939) Adventure|Children|Fantasy|Musical 1 919 5.0 4.4044876 923 Citizen Kane (1941) Drama|Mystery 1 923 5.0 4.4456143 940 Adventures of Robin Hood, The (1938) Action|Adventure|Romance 1 940 5.0 4.5667586 943 Ghost and Mrs. Muir, The (1947) Drama|Fantasy|Romance 1 943 4.0 4.4622855 954 Mr. Smith Goes to Washington (1939) Drama 1 954 5.0 4.6446753 1009 Escape to Witch Mountain (1975) Adventure|Children|Fantasy 1 1009 3.0 3.3845632 1023 Winnie the Pooh and the Blustery Day (1968) Animation|Children|Musical 1 1023 5.0 3.8209221 1024 Three Caballeros, The (1945) Animation|Children|Musical 1 1024 5.0 4.061979 1025 Sword in the Stone, The (1963) Animation|Children|Fantasy|Musical 1 1025 5.0 4.1289725 1029 Dumbo (1941) Animation|Children|Drama|Musical 1 1029 5.0 3.8364646 1030 Pete's Dragon (1977) Adventure|Animation|Children|Musical 1 1030 3.0 2.962204 1031 Bedknobs and Broomstic

## Recommend moive to users with id: 575, 232. 
you can choose some users to recommend the moives 

In [0]:
# Install and import Koalas if needed
!pip install koalas
import databricks.koalas as ks


You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-ad835de6-aba4-4ad2-b73e-ffe98ed5af83/bin/python -m pip install --upgrade pip' command.


In [0]:
userRecs = bestModel.recommendForAllUsers(10)

# Convert PySpark DataFrames to Koalas DataFrames
userRecs_ks = userRecs.to_koalas()
movies_ks = movies_df.to_koalas()

def movieRecommendation(inputId):
  recs_list=[]
  for recs in userRecs_ks.loc[str(inputId), 'recommendations']:
    recs_list.append(str(recs[0]))
  return (movies_ks[movies_ks['movieId'].isin(recs_list)])


In [0]:
# Get top movie recommendations for user with ID 148
recommended_movies_148 = movieRecommendation(85)
print("Top recommendations for user 148:")
print(recommended_movies_148)

---------------------------------------------------------------------------
KeyError                                  Traceback (most recent call last)
File <command-3567679698529084>:2
      1 # Get top movie recommendations for user with ID 148
----> 2 recommended_movies_148 = movieRecommendation(85)
      3 print("Top recommendations for user 148:")
      4 print(recommended_movies_148)

File <command-3567679698529085>:10, in movieRecommendation(inputId)
      8 recs_list=[]
      9 for recs in userRecs_ks.loc[str(inputId), 'recommendations']:
---> 10   recs_list.append(str(recs[0]))
     11 return (movies_ks[movies_ks['movieId'].isin(recs_list)])

KeyError: 0

In [0]:
print(userRecs_ks.index.unique())


Int64Index([148, 463, 471, 496, 243, 392, 540,  31, 516,  85,
            ...
            521,  36, 187, 208, 315, 393,  89, 401, 422, 517],
           dtype='int64', name='userId', length=610)


## Find the similar moives for moive with id: 463, 471
You can find the similar moives based on the ALS results

In [0]:
itemFactors=bestModel.itemFactors.to_koalas()

In [0]:
def similarMovies(inputId, matrix='cosine_similarity'):
  try:
    movieFeature=itemFactors.loc[itemFactors.id==str(inputId),'features'].to_numpy()[0]
  except:
    return 'There is no movie with id ' + str(inputId)
  
  if matrix=='cosine_similarity':
    similarMovie=pd.DataFrame(columns=('movieId','cosine_similarity'))
    for id,feature in itemFactors.to_numpy():
      cs=np.dot(movieFeature,feature)/(np.linalg.norm(movieFeature) * np.linalg.norm(feature))
      similarMovie=similarMovie.append({'movieId':str(id), 'cosine_similarity':cs}, ignore_index=True)
    similarMovie_cs=similarMovie.sort_values(by=['cosine_similarity'],ascending = False)[1:11]
    joint=similarMovie_cs.merge(movies_ks.to_pandas(), left_on='movieId', right_on = 'movieId', how = 'inner')
  if matrix=='euclidean_distance':
    similarMovie=pd.DataFrame(columns=('movieId','euclidean_distance'))
    for id,feature in itemFactors.to_numpy():
      ed=np.linalg.norm(np.array(movieFeature)-np.array(feature))
      similarMovie=similarMovie.append({'movieId':str(id), 'euclidean_distance':ed}, ignore_index=True)
    similarMovie_ed=similarMovie.sort_values(by=['euclidean_distance'])[1:11]
    joint=similarMovie_ed.merge(movies_ks.to_pandas(), left_on='movieId', right_on = 'movieId', how = 'inner')
  return joint[['movieId','title','genres']]

In [0]:
similarMovies(463)

Out[80]: 'There is no movie with id 463'

In [0]:
print('Similar movies based on cosine similarity matrix are as follows.')
similarMovies(471, 'cosine_similarity')

Similar movies based on cosine similarity matrix are as follows.


<command-3567679698529087>:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similarMovie=similarMovie.append({'movieId':str(id), 'cosine_similarity':cs}, ignore_index=True)
<command-3567679698529087>:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similarMovie=similarMovie.append({'movieId':str(id), 'cosine_similarity':cs}, ignore_index=True)
<command-3567679698529087>:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similarMovie=similarMovie.append({'movieId':str(id), 'cosine_similarity':cs}, ignore_index=True)
<command-3567679698529087>:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similarMovie=similarMovie.append({'movieId':s

movieId 
 title 
 genres 
 
 
 
 
 0 
 475 
 In the Name of the Father (1993) 
 Drama 
 
 
 1 
 3479 
 Ladyhawke (1985) 
 Adventure|Fantasy|Romance 
 
 
 2 
 224 
 Don Juan DeMarco (1995) 
 Comedy|Drama|Romance 
 
 
 3 
 1305 
 Paris, Texas (1984) 
 Drama|Romance 
 
 
 4 
 2147 
 Clan of the Cave Bear, The (1986) 
 Adventure|Drama|Fantasy 
 
 
 5 
 3194 
 Way We Were, The (1973) 
 Drama|Romance 
 
 
 6 
 46967 
 Scoop (2006) 
 Comedy|Fantasy|Mystery 
 
 
 7 
 49347 
 Fast Food Nation (2006) 
 Drama 
 
 
 8 
 27821 
 Interpreter, The (2005) 
 Drama|Thriller 
 
 
 9 
 345 
 Adventures of Priscilla, Queen of the Desert, ... 
 Comedy|Drama


## Write the report 
motivation: As artificial intelligence pervails in internet industry, more and more ecommerce platforms start to characterize their recommendation systems in order to provide better service. Collaborative filtering is one of the most popular recommendation algorithm which can be implemented with Alternating Least Squares (ALS) model in Spark ML. It would be a interesting and significant attempt to create a movie recommender for movie rating sites users.

step1. Data ETL and Data Exploration

I firstly loaded the rating data, established corresponding spark dataframes and checked out the basic information of the dataset.

step2. Online Analytical Processing

I performed analysis on the dataset from multi angle and gained some intuitive insights.

step3. Model Selection

I built up the ALS model and tuned the hyperparameter using 5-fold cross-validation, applying the optimal hyperparameters on the best final model.

step4. Model Evaluation

Finally, I evaluated the recommendation model by measuring the root-mean-square error of rating prediction on the testset.

step5. Model Application: Recommend moive to users

For given users, I wrote a function to dirctly recommend 10 movies which they may be interested in based on the model.

step6. Model Application: Find the similar moives

I also applid the ALS results on finding the similar moives for a given movie. I used two matrix to evaluate the similarity between movies: cosine similarity and euclidean distance, which can be used sperately depends on situations.

Output and Conclusion

In this project, I built a ALS model with Spark APIs based on MovieLens dataset, predicted the ratings for the movies and made specific recommendation to users accordingly. The RMSE of the best model is approximately 0.88.